In [13]:
import random
import simpy
import matplotlib.pyplot as plt
import pandas as pd

# Stochastic Parameters with expected values
PROCESSING_TIME_MEAN = 83.70  # seconds
TBF_MEAN = 3600  # expected time between failures (seconds)
TTR_MEAN = 30  # expected time to repair (seconds)
JOB_ARRIVAL_RATE = 20  # jobs per second
NUM_MACHINES = 10
STARTUP_MEAN=30

# Power consumption rates (kW)
POWER_CONSUMPTION = {
    'busy': 15,
    'idle': 9.3,
    'startup': 10,
    'standby': 0,
    'failed': 0
}

# Global data structure to collect machine states and energy consumption
data = []

# Machine states
machines = []


In [14]:
# Data collection
def collect_data(env, machine):
     
     total_energy = 0
     for state, time in machine['time_in_states'].items():

        time_hours=0

        if state==machine['state']:
          time_hours = time
          time_hours_energy= time_hours

          total_energy += POWER_CONSUMPTION[state] * (time_hours_energy)
        
          data.append({
         'time': env.now,
         'machine_id': machine['id'],
         'state': machine['state'],
         'MS': state,
         'time_in_preocess': time_hours,
         'energy':total_energy})

for i in range(NUM_MACHINES):
    machines.append({
        'id': i,
        'state': 'idle',  # Start machines in idle state
        'total_energy': 0,
        'time_in_states': {'busy': 0, 'idle': 0, 'startup': 0, 'standby': 0, 'failed': 0}, 
        'cumprocessingtime':0, 'failuretime':random.expovariate(1.0 / TBF_MEAN) 
    })



In [15]:
def machine_run(env, machine, buffer):

    while True:

        if machine['state'] == 'idle':
            
            if len(buffer.items) > 0:

                yield buffer.get()  # Get a job from the buffer
                machine['state'] = 'busy'
                
                processing_time = random.expovariate(1.0 / PROCESSING_TIME_MEAN)
                if machine['cumprocessingtime']+processing_time <= machine['failuretime']:
                    machine['cumprocessingtime']=processing_time+machine['cumprocessingtime']

                    yield env.timeout(processing_time)

                    machine['time_in_states']['busy'] = processing_time
                    collect_data(env, machine)
                    machine['state'] = 'idle'
                   
                else:

                    failure_time_remaining = machine['failuretime'] - machine['cumprocessingtime']
                    machine['state'] = 'busy'

                    yield env.timeout(failure_time_remaining)

                    machine['time_in_states']['busy'] = failure_time_remaining
                    machine['cumprocessingtime']=0
                    machine['failuretime']= random.expovariate(1.0 / TBF_MEAN)
                    collect_data(env, machine)
                   

                    machine['state'] = 'failed'
                    repair_time = random.expovariate(1.0 / TTR_MEAN)

                    yield env.timeout(repair_time)

                    machine['time_in_states']['failed'] = repair_time 
                    collect_data(env, machine)
                    machine['state'] ='idle'

            else:
                yield env.timeout(1)  # Wait 1 unit of time if no job
                machine['time_in_states']['idle'] = 1
                collect_data(env, machine)


def arrival_process(env, buffer):
    while True:
        yield env.timeout(random.expovariate(1.0 / JOB_ARRIVAL_RATE))
        #yield env.timeout(1)  
        buffer.put(1) 

In [16]:
# Setup the simulation environment
env = simpy.Environment()
buffer = simpy.Store(env, capacity=10)  # Infinite capacity buffer

# Start the arrival process
env.process(arrival_process(env, buffer))

# Start the machine processes
for machine in machines:
    env.process(machine_run(env, machine, buffer))

# Run the simulation for a given amount of time
simulation_time = 10000  # seconds 
env.run(until=simulation_time)

In [17]:
# Create a plot for each machine
df = pd.DataFrame(data)

Data_selected_0= df[df['machine_id']==0]
Data_selected_1= df[df['machine_id']==1]
Data_selected_2= df[df['machine_id']==2]
Data_selected_3= df[df['machine_id']==3]
Data_selected_4= df[df['machine_id']==4]
Data_selected_5= df[df['machine_id']==5]

fig, ax = plt.subplots(figsize=(12, 6), dpi=1000)

# Define color mapping for states
color_map = {"idle": "green", "busy": "blue", "failed": "red"}

# Plot state transitions for each machine
for machine_id in df["machine_id"].unique():
    machine_data = df[df["machine_id"] == machine_id]
    for i in range(len(machine_data) - 1):
        start_time = machine_data.iloc[i]["time"]
        end_time = machine_data.iloc[i + 1]["time"]
        state = machine_data.iloc[i+1]["state"]
        ax.plot([start_time, end_time], [machine_id, machine_id], color=color_map[state], linewidth=4)

# Customize the plotax.set_yticks(df["machine_id"].unique())
ax.set_yticks(df["machine_id"].unique())
ax.set_yticklabels([f"Machine {i}" for i in df["machine_id"].unique()])
ax.set_xlabel("Time (s)")
ax.set_ylabel("Machine ID")
ax.set_title("Machine State Transitions Over Time")
ax.grid(True)

# Add legend
custom_lines = [plt.Line2D([0], [0], color=color_map[state], lw=4) for state in color_map]
ax.legend(custom_lines, list(color_map.keys()))



# Display the plot
plt.show()



c:\Users\220425984\AppData\Local\anaconda3\Lib\site-packages\IPython\core\pylabtools.py:170: UserWarning: Creating legend with loc="best" can be slow with large amounts of data.
  fig.canvas.print_figure(bytes_io, **kw)


In [64]:
import matplotlib.pyplot as plt

fig, ax = plt.subplots(figsize=(12, 6), dpi=1000)

ax.plot(df['time'], df['energy'], color='b')

ax.set_xlabel("Time (s)")
ax.set_ylabel("Energy Consumption")
ax.set_title("Total Energy Consumption")
ax.legend()

# Display the plot
plt.show()

No artists with labels found to put in legend.  Note that artists whose label start with an underscore are ignored when legend() is called with no argument.


In [65]:
machine_0 = df[df["machine_id"] == 0]
machine_1 = df[df["machine_id"] == 1]
machine_2 = df[df["machine_id"] == 2]
machine_3 = df[df["machine_id"] == 3]
machine_4 = df[df["machine_id"] == 4]

import matplotlib.pyplot as plt

# Assuming 'df' is your dataframe and it's already defined
machine_ids = df["machine_id"].unique()
color_list = ['r', 'b', 'g', 'y', 'm']  # Adding more colors to accommodate all machines

fig, ax = plt.subplots(figsize=(12, 6), dpi=1000)

for machine_id, color in zip(machine_ids, color_list):
    machine_data = df[df["machine_id"] == machine_id]
    ax.plot(machine_data['time'], machine_data['energy'], color=color, label=f"Machine {machine_id}")

ax.set_xlabel("Time (s)")
ax.set_ylabel("Energy Consumption")
ax.set_title("The Energy Consumption of Machines")
ax.legend()

# Display the plot
plt.show()



